In [17]:
# загрузим библиотеки и установим опции
from __future__ import division, print_function
# отключим всякие предупреждения Anaconda
import warnings
warnings.filterwarnings('ignore')
#%matplotlib inline
import numpy as np
import pandas as pd
from sklearn.metrics import roc_auc_score

In [18]:
# загрузим обучающую и тестовую выборки
train_df = pd.read_csv('train_sessions.csv')#,index_col='session_id')
test_df = pd.read_csv('test_sessions.csv')#, index_col='session_id')

# приведем колонки time1, ..., time10 к временному формату
times = ['time%s' % i for i in range(1, 11)]
train_df[times] = train_df[times].apply(pd.to_datetime)
test_df[times] = test_df[times].apply(pd.to_datetime)

# отсортируем данные по времени
train_df = train_df.sort_values(by='time1')

# посмотрим на заголовок обучающей выборки
train_df.head()

session_id  site1               time1  site2               time2  \
21668        21669     56 2013-01-12 08:05:57   55.0 2013-01-12 08:05:57   
54842        54843     56 2013-01-12 08:37:23   55.0 2013-01-12 08:37:23   
77291        77292    946 2013-01-12 08:50:13  946.0 2013-01-12 08:50:14   
114020      114021    945 2013-01-12 08:50:17  948.0 2013-01-12 08:50:17   
146669      146670    947 2013-01-12 08:50:20  950.0 2013-01-12 08:50:20   

        site3               time3  site4               time4  site5  ...  \
21668     NaN                 NaT    NaN                 NaT    NaN  ...   
54842    56.0 2013-01-12 09:07:07   55.0 2013-01-12 09:07:09    NaN  ...   
77291   951.0 2013-01-12 08:50:15  946.0 2013-01-12 08:50:15  946.0  ...   
114020  949.0 2013-01-12 08:50:18  948.0 2013-01-12 08:50:18  945.0  ...   
146669  948.0 2013-01-12 08:50:20  947.0 2013-01-12 08:50:21  950.0  ...   

                     time6  site7               time7  site8  \
21668                  NaT    NaN                 NaT    NaN   
54842                  NaT    NaN                 NaT    NaN   
77291  2013-01-12 08:50:16  948.0 2013-01-12 08:50:16  784.0   
114020 2013-01-12 08:50:18  947.0 2013-01-12 08:50:19  945.0   
146669 2013-01-12 08:50:21  946.0 2013-01-12 08:50:21  951.0   

                     time8  site9               time9  site10  \
21668                  NaT    NaN                 NaT     NaN   
54842                  NaT    NaN                 NaT     NaN   
77291  2013-01-12 08:50:16  949.0 2013-01-12 08:50:17   946.0   
114020 2013-01-12 08:50:19  946.0 2013-01-12 08:50:19   946.0   
146669 2013-01-12 08:50:22  946.0 2013-01-12 08:50:22   947.0   

                    time10  target  
21668                  NaT       0  
54842                  NaT       0  
77291  2013-01-12 08:50:17       0  
114020 2013-01-12 08:50:20       0  
146669 2013-01-12 08:50:22       0  

[5 rows x 22 columns]

In [19]:
sites = ['site%s' % i for i in range(1, 11)]
#заменим nan на 0
train_df[sites] = train_df[sites].fillna(0).astype('int').astype('str')
test_df[sites] = test_df[sites].fillna(0).astype('int').astype('str')
#создадим тексты необходимые для обучения word2vec
train_df['list'] = train_df['site1']
test_df['list'] = test_df['site1']
for s in sites[1:]:
    train_df['list'] = train_df['list']+","+train_df[s]
    test_df['list'] = test_df['list']+","+test_df[s]
train_df['list_w'] = train_df['list'].apply(lambda x: x.split(','))
test_df['list_w'] = test_df['list'].apply(lambda x: x.split(','))

In [20]:
#В нашем случае предложение это набор сайтов, которые посещал пользователь
#нам необязательно переводить цифры в названия сайтов, т.к. алгоритм будем выявлять взаимосвязь их друг с другом.
train_df['list_w'][10]

['229', '1500', '33', '1500', '391', '35', '29', '2276', '40305', '23']

In [21]:
# подключим word2vec
from gensim.models import word2vec

In [22]:
#объединим обучающую и тестовую выборки и обучим нашу модель на всех данных 
#с размером окна в 6=3*2 (длина предложения 10 слов) и итоговыми векторами размерности 300, параметр workers отвечает за количество ядер
test_df['target'] = -1
data = pd.concat([train_df,test_df], axis=0)

model = word2vec.Word2Vec(data['list_w'], vector_size=300, window=3, workers=4)
#создадим словарь со словами и соответсвующими им векторами
w2v = dict(zip(model.wv.index_to_key, model.wv.vectors))

In [23]:
w2v

{'0': array([-1.38577029e-01,  6.45565018e-02, -1.52628958e-01,  2.68896073e-01,
         8.67565349e-03, -2.60897309e-01,  8.18731308e-01,  3.30537438e-01,
        -3.67697537e-01,  1.03162527e-01,  3.06721628e-01,  1.55462638e-01,
        -1.97415099e-01,  2.10704923e-01, -2.83629686e-01, -2.05693617e-01,
        -1.86763301e-01, -1.16147429e-01,  5.09234257e-02, -6.44294977e-01,
         5.03681540e-01,  3.10793430e-01,  1.84111178e-01, -6.43531740e-01,
        -4.99523594e-04,  5.26054442e-01, -4.16668028e-01, -2.78378632e-02,
        -4.84938979e-01, -2.19919339e-01, -1.61959901e-02, -4.88270581e-01,
        -5.35566509e-02, -6.38973475e-01,  4.83931273e-01,  3.58764172e-01,
         6.18010879e-01, -3.28821898e-01, -1.54291481e-01,  2.38287076e-01,
        -3.55175704e-01,  5.00194371e-01, -2.04625458e-01,  2.49115184e-01,
         2.37677887e-01, -2.68170476e-01, -2.32829049e-01,  1.50548190e-01,
        -3.68040681e-01,  7.61048734e-01, -1.15638718e-01, -2.69961983e-01,
       

In [24]:
class mean_vectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        self.dim = len(next(iter(w2v.values())))

    def fit(self, X):
        return self 

    def transform(self, X):
        return np.array([
            np.mean([self.word2vec[w] for w in words if w in self.word2vec] 
                    or [np.zeros(self.dim)], axis=0)
            for words in X
        ])

In [25]:
data_mean=mean_vectorizer(w2v).fit(train_df['list_w']).transform(train_df['list_w'])
data_mean.shape

(253561, 300)

In [26]:
# Воспользуемся валидацией
def split(train,y,ratio):
    idx = round(train.shape[0] * ratio)
    return train[:idx, :], train[idx:, :], y[:idx], y[idx:]
y = train_df['target']
Xtr, Xval, ytr, yval = split(data_mean, y,0.8)
Xtr.shape,Xval.shape,ytr.mean(),yval.mean()

((202849, 300), (50712, 300), 0.009726446765820882, 0.006389020350212968)

In [27]:
# подключим библиотеки keras 
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Activation, Input
from keras.preprocessing.text import Tokenizer
from keras import regularizers

In [28]:
# опишем нейронную сеть
model = Sequential()
model.add(Dense(128, input_dim=(Xtr.shape[1])))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(1))
model.add(Activation('sigmoid'))
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['binary_accuracy'])

In [29]:
history = model.fit(Xtr, ytr,
                    batch_size=128,
                    epochs=10,
                    validation_data=(Xval, yval),
                    
                    verbose=0)

In [30]:
classes = model.predict(Xval, batch_size=128)
roc_auc_score(yval, classes)

0.9221110233967131

In [31]:
import xgboost as xgb


In [32]:
# !pip install xgboost

In [33]:
dtr = xgb.DMatrix(Xtr, label= ytr,missing = np.nan)
dval = xgb.DMatrix(Xval, label= yval,missing = np.nan)
watchlist = [(dtr, 'train'), (dval, 'eval')]
history = dict()

In [34]:
params = {
    'max_depth': 26,
    'eta': 0.025,
    'nthread': 4,
    'gamma' : 1,
    'alpha' : 1,
    'subsample': 0.85,
    'eval_metric': ['auc'],
    'objective': 'binary:logistic',
    'colsample_bytree': 0.9,
    'min_child_weight': 100,
    'scale_pos_weight':(1)/y.mean(),
    'seed':7
}

In [40]:
model_new = xgb.train(params, dtr, num_boost_round=200, evals=watchlist, evals_result=history, verbose_eval=20)


[0]	train-auc:0.95620	eval-auc:0.84209
[20]	train-auc:0.99029	eval-auc:0.91552
[40]	train-auc:0.99293	eval-auc:0.91573
[60]	train-auc:0.99453	eval-auc:0.91811
[80]	train-auc:0.99568	eval-auc:0.92102
[100]	train-auc:0.99657	eval-auc:0.92319


KeyboardInterrupt: 

In [44]:
from sklearn.linear_model import LogisticRegression
def get_auc_lr_valid(X, y, C=1, seed=7, ratio = 0.8):
    # разделим выборку на обучающую и валидационную
    idx = round(X.shape[0] * ratio)
    # обучение классификатора
    lr = LogisticRegression(C=C, random_state=seed, n_jobs=-1).fit(X[:idx], y[:idx])
    # прогноз для валидационной выборки
    y_pred = lr.predict_proba(X[idx:, :])[:, 1]
    # считаем качество
    score = roc_auc_score(y[idx:], y_pred)

    return score

In [45]:
get_auc_lr_valid(data_mean, y, C=1, seed=7, ratio = 0.8)


0.9118318086218843

In [41]:
#пропишем класс выполняющий tfidf преобразование.
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import defaultdict

class tfidf_vectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        self.word2weight = None
        self.dim = len(next(iter(w2v.values())))

    def fit(self, X):
        tfidf = TfidfVectorizer(analyzer=lambda x: x)
        tfidf.fit(X)
        max_idf = max(tfidf.idf_)
        self.word2weight = defaultdict(
            lambda: max_idf,
            [(w, tfidf.idf_[i]) for w, i in tfidf.vocabulary_.items()])

        return self

    def transform(self, X):
        return np.array([
                np.mean([self.word2vec[w] * self.word2weight[w]
                         for w in words if w in self.word2vec] or
                        [np.zeros(self.dim)], axis=0)
                for words in X
            ])

In [42]:
data_mean = tfidf_vectorizer(w2v).fit(train_df['list_w']).transform(train_df['list_w'])


In [43]:
get_auc_lr_valid(data_mean, y, C=1, seed=7, ratio = 0.8)


NameError: name 'get_auc_lr_valid' is not defined

In [35]:
Xtrain = pd.read_csv('train_content.csv')
Xtest = pd.read_csv('test_content.csv')
print(Xtrain.shape,Xtest.shape)
Xtrain.head()

FileNotFoundError: [Errno 2] No such file or directory: 'train_content.csv'

In [1]:
import tensorflow as tf

# Check for GPU availability
print("Num GPUs Available:", len(tf.config.experimental.list_physical_devices('GPU')))

# Print GPU information
print(tf.test.gpu_device_name())


Num GPUs Available: 1
/device:GPU:0


In [15]:
import tensorflow as tf

# Load and preprocess the MNIST dataset
(train_images, train_labels), (test_images, test_labels) = tf.keras.datasets.mnist.load_data()
train_images, test_images = train_images / 255.0, test_images / 255.0

# Flatten the images
train_images = train_images.reshape((train_images.shape[0], -1))
test_images = test_images.reshape((test_images.shape[0], -1))

# Build the model
model = tf.keras.Sequential([
    tf.keras.layers.Dense(128, activation='relu', input_shape=(784,)),
    tf.keras.layers.Dropout(0.2),
    tf.keras.layers.Dense(10)
])

# Compile the model
model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

# Train the model
model.fit(train_images, train_labels, epochs=5)


Epoch 1/5
1875/1875 [==============================] - 3s 2ms/step - loss: 0.2970 - accuracy: 0.9129
Epoch 2/5
1198/1875 [==================>...........] - ETA: 1s - loss: 0.1464 - accuracy: 0.9565

KeyboardInterrupt: 

In [16]:
import tensorflow as tf
physical_devices = tf.config.list_physical_devices('GPU')
if len(physical_devices) > 0:
    tf.config.experimental.set_memory_growth(physical_devices[0], True)
    print(f"Num GPUs Available: {len(physical_devices)}")
else:
    print("No GPU devices found.")


Num GPUs Available: 1


In [11]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "-1"

In [12]:
import tensorflow as tf

# Check for GPU availability
print("Num GPUs Available:", len(tf.config.experimental.list_physical_devices('GPU')))

# Print GPU information
print(tf.test.gpu_device_name())


Num GPUs Available: 1
/device:GPU:0


In [13]:
gpus = tf.config.experimental.list_physical_devices('GPU')


In [14]:
import tensorflow as tf

# Explicitly set GPU configurations
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
    try:
        # Currently, memory growth needs to be the same across GPUs
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
        logical_gpus = tf.config.experimental.list_logical_devices('GPU')
        print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
    except RuntimeError as e:
        # Memory growth must be set before GPUs have been initialized
        print(e)


1 Physical GPUs, 1 Logical GPUs


In [10]:
from tensorflow.python.client import device_lib 
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 5327811399013843989
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 1731618407
locality {
  bus_id: 1
  links {
  }
}
incarnation: 302182578741514461
physical_device_desc: "device: 0, name: NVIDIA GeForce RTX 3050 Laptop GPU, pci bus id: 0000:01:00.0, compute capability: 8.6"
]
